# Predict Ovulatory Disorders

Age_(yrs): The age of the woman.
BMI: Body Mass Index, indicating body fat based on height and weight.
AMH(ng/mL): Anti-Müllerian Hormone levels, reflecting ovarian reserve.
PCOS_(Y/N): Whether the woman has been diagnosed with PCOS.
Cycle_length(days): The length of the menstrual cycle.

In [17]:
# Import necessary libraries
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.metrics import accuracy_score, f1_score, classification_report
from imblearn.over_sampling import SMOTE
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.dummy import DummyClassifier
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer

In [2]:
import warnings
warnings.filterwarnings('ignore')

# Step 1: Load Dataset
df = pd.read_csv('../datasets/PCOS_data.csv')

In [3]:
# Step 2: Normalize column names
df.columns = df.columns.str.strip().str.replace(' ', '_')

# Step 3: Handle numeric columns
numeric_columns = ['BMI', 'Age_(yrs)', 'AMH(ng/mL)', 'FSH(mIU/mL)', 'LH(mIU/mL)', 'Cycle_length(days)', 'TSH_(mIU/L)']
for col in numeric_columns:
    df[col] = pd.to_numeric(df[col], errors='coerce')

# Impute missing values with median
imputer = SimpleImputer(strategy='median')
df[numeric_columns] = imputer.fit_transform(df[numeric_columns])

# Handle categorical columns and fill missing values with mode
categorical_columns = ['PCOS_(Y/N)', 'Blood_Group']
for col in categorical_columns:
    df[col] = df[col].fillna(df[col].mode()[0])

# Encode categorical columns
labelencoder = LabelEncoder()
df[categorical_columns] = df[categorical_columns].apply(labelencoder.fit_transform)

In [4]:
# Step 4: Define features and target for classification
X = df[['Age_(yrs)', 'BMI', 'AMH(ng/mL)', 'PCOS_(Y/N)', 'Cycle_length(days)']]
y = (df['FSH(mIU/mL)'] / df['LH(mIU/mL)'] > 1).astype(int)  # Binary classification based on FSH/LH ratio

# Step 5: Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

In [5]:
# Step 6: Scale the features
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)


In [6]:
# Step 7: Apply SMOTE for class balancing
smote = SMOTE(random_state=42)
X_train_smote, y_train_smote = smote.fit_resample(X_train_scaled, y_train)

In [7]:
# Step 8: Define classifiers with basic hyperparameters
classifiers = {
    'Random Forest': RandomForestClassifier(n_estimators=200, max_depth=15, random_state=42),
    'XGBoost': XGBClassifier(use_label_encoder=False, eval_metric='logloss', n_estimators=200, max_depth=10),
    'LightGBM': LGBMClassifier(n_estimators=200, max_depth=10),
    'CatBoost': CatBoostClassifier(verbose=0, n_estimators=200, max_depth=10),
    'KNN (k=5)': KNeighborsClassifier(n_neighbors=5),
    'KNN (k=3)': KNeighborsClassifier(n_neighbors=3),
    'Decision Tree (gini)': DecisionTreeClassifier(criterion='gini'),
    'Decision Tree (entropy)': DecisionTreeClassifier(criterion='entropy'),
    'Naive Bayes': GaussianNB(),
    'Dummy Classifier': DummyClassifier(strategy='most_frequent')
}

In [8]:
# Step 9: Train and evaluate classifiers
results = {}
f1_scores = {}

for name, clf in classifiers.items():
    clf.fit(X_train_smote, y_train_smote)
    y_pred = clf.predict(X_test_scaled)
    
    accuracy = accuracy_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    
    results[name] = accuracy
    f1_scores[name] = f1
    print(f'{name} - Accuracy: {accuracy:.4f}, F1 Score: {f1:.4f}')


Random Forest - Accuracy: 0.8349, F1 Score: 0.9072
XGBoost - Accuracy: 0.8165, F1 Score: 0.8969
[LightGBM] [Info] Number of positive: 378, number of negative: 378
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000062 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 841
[LightGBM] [Info] Number of data points in the train set: 756, number of used features: 5
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No

In [9]:
# Display results
results_df = pd.DataFrame(list(results.items()), columns=['Classifier', 'Accuracy'])
f1_scores_df = pd.DataFrame(list(f1_scores.items()), columns=['Classifier', 'F1 Score'])

# Sort by accuracy and display
print("Accuracy Results:")
print(results_df.sort_values(by='Accuracy', ascending=False))

print("\nF1 Score Results:")
print(f1_scores_df.sort_values(by='F1 Score', ascending=False))


Accuracy Results:
                Classifier  Accuracy
0            Random Forest  0.834862
2                 LightGBM  0.834862
1                  XGBoost  0.816514
3                 CatBoost  0.770642
6     Decision Tree (gini)  0.770642
8              Naive Bayes  0.770642
5                KNN (k=3)  0.733945
7  Decision Tree (entropy)  0.715596
4                KNN (k=5)  0.660550
9         Dummy Classifier  0.128440

F1 Score Results:
                Classifier  F1 Score
2                 LightGBM  0.908163
0            Random Forest  0.907216
1                  XGBoost  0.896907
3                 CatBoost  0.866310
6     Decision Tree (gini)  0.864865
8              Naive Bayes  0.857143
5                KNN (k=3)  0.837989
7  Decision Tree (entropy)  0.828729
4                KNN (k=5)  0.778443
9         Dummy Classifier  0.000000


In [10]:
# Step 10: Display classification report for the best performing model (replace 'Random Forest' with the best one)
best_model = classifiers['Random Forest']
y_pred_best = best_model.predict(X_test_scaled)
print(classification_report(y_test, y_pred_best))

              precision    recall  f1-score   support

           0       0.30      0.21      0.25        14
           1       0.89      0.93      0.91        95

    accuracy                           0.83       109
   macro avg       0.59      0.57      0.58       109
weighted avg       0.81      0.83      0.82       109



# Hyperparameter tuning 

In [11]:
import optuna
from sklearn.model_selection import cross_val_score


In [12]:
# Random Forest Tuning
def rf_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 5, 20),
        'min_samples_split': trial.suggest_int('min_samples_split', 2, 10),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 4),
        'bootstrap': trial.suggest_categorical('bootstrap', [True, False])
    }
    rf = RandomForestClassifier(**params, random_state=42)
    score = cross_val_score(rf, X_train_scaled, y_train, cv=5, scoring='accuracy').mean()
    return score

# XGBoost Tuning
def xgb_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 5, 15),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0)
    }
    xgb = XGBClassifier(**params, use_label_encoder=False, eval_metric='logloss', random_state=42)
    score = cross_val_score(xgb, X_train_scaled, y_train, cv=5, scoring='accuracy').mean()
    return score

# LightGBM Tuning
def lgbm_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 5, 15),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 31, 150),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0)
    }
    lgbm = LGBMClassifier(**params, random_state=42)
    score = cross_val_score(lgbm, X_train_scaled, y_train, cv=5, scoring='accuracy').mean()
    return score

# CatBoost Tuning
def catboost_objective(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 100, 500),
        'depth': trial.suggest_int('depth', 5, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-5, 10)
    }
    catboost = CatBoostClassifier(**params, verbose=0, random_state=42)
    score = cross_val_score(catboost, X_train_scaled, y_train, cv=5, scoring='accuracy').mean()
    return score


In [13]:
# Running Optuna for each model

# Random Forest
print("Tuning Random Forest...")
rf_study = optuna.create_study(direction='maximize')
rf_study.optimize(rf_objective, n_trials=50)
best_rf_params = rf_study.best_trial.params
print(f"Best Random Forest params: {best_rf_params}")

# XGBoost
print("Tuning XGBoost...")
xgb_study = optuna.create_study(direction='maximize')
xgb_study.optimize(xgb_objective, n_trials=50)
best_xgb_params = xgb_study.best_trial.params
print(f"Best XGBoost params: {best_xgb_params}")

# LightGBM
print("Tuning LightGBM...")
lgbm_study = optuna.create_study(direction='maximize')
lgbm_study.optimize(lgbm_objective, n_trials=50)
best_lgbm_params = lgbm_study.best_trial.params
print(f"Best LightGBM params: {best_lgbm_params}")

# CatBoost
print("Tuning CatBoost...")
catboost_study = optuna.create_study(direction='maximize')
catboost_study.optimize(catboost_objective, n_trials=50)
best_catboost_params = catboost_study.best_trial.params
print(f"Best CatBoost params: {best_catboost_params}")


[I 2024-10-15 21:03:42,731] A new study created in memory with name: no-name-51c4f443-3e96-4add-aa6d-6b63e15efb54


Tuning Random Forest...


[I 2024-10-15 21:03:43,854] Trial 0 finished with value: 0.875006682705159 and parameters: {'n_estimators': 414, 'max_depth': 7, 'min_samples_split': 2, 'min_samples_leaf': 3, 'bootstrap': True}. Best is trial 0 with value: 0.875006682705159.
[I 2024-10-15 21:03:44,273] Trial 1 finished with value: 0.8727345629510825 and parameters: {'n_estimators': 177, 'max_depth': 9, 'min_samples_split': 7, 'min_samples_leaf': 2, 'bootstrap': False}. Best is trial 0 with value: 0.875006682705159.
[I 2024-10-15 21:03:44,880] Trial 2 finished with value: 0.8773322641005079 and parameters: {'n_estimators': 253, 'max_depth': 14, 'min_samples_split': 7, 'min_samples_leaf': 4, 'bootstrap': False}. Best is trial 2 with value: 0.8773322641005079.
[I 2024-10-15 21:03:45,618] Trial 3 finished with value: 0.8773857257417802 and parameters: {'n_estimators': 303, 'max_depth': 19, 'min_samples_split': 2, 'min_samples_leaf': 3, 'bootstrap': False}. Best is trial 3 with value: 0.8773857257417802.
[I 2024-10-15 21:0

Best Random Forest params: {'n_estimators': 214, 'max_depth': 16, 'min_samples_split': 9, 'min_samples_leaf': 3, 'bootstrap': False}
Tuning XGBoost...


[I 2024-10-15 21:04:13,197] Trial 0 finished with value: 0.8750868751670676 and parameters: {'n_estimators': 270, 'max_depth': 15, 'learning_rate': 0.1279760871789719, 'subsample': 0.6595223419733703, 'colsample_bytree': 0.7392890353552655}. Best is trial 0 with value: 0.8750868751670676.
[I 2024-10-15 21:04:13,504] Trial 1 finished with value: 0.87043571237637 and parameters: {'n_estimators': 314, 'max_depth': 8, 'learning_rate': 0.2597572753489605, 'subsample': 0.6248023417637284, 'colsample_bytree': 0.795535073810318}. Best is trial 0 with value: 0.8750868751670676.
[I 2024-10-15 21:04:13,931] Trial 2 finished with value: 0.8611333867949744 and parameters: {'n_estimators': 491, 'max_depth': 11, 'learning_rate': 0.29081159762608727, 'subsample': 0.5963148457841474, 'colsample_bytree': 0.5861740906614494}. Best is trial 0 with value: 0.8750868751670676.
[I 2024-10-15 21:04:14,224] Trial 3 finished with value: 0.8726811013098101 and parameters: {'n_estimators': 229, 'max_depth': 6, 'le

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-10-15 21:04:43,794] Trial 49 finished with value: 0.8748997594226143 and parameters: {'n_estimators': 390, 'max_depth': 8, 'learning_rate': 0.02411022894305547, 'num_leaves': 118, 'subsample': 0.9754348294327824}. Best is trial 33 with value: 0.881903234429297.
[I 2024-10-15 21:04:43,794] A new study created in memory with name: no-name-8a09ee6e-b295-4076-b313-1e73481374fa


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-10-15 21:04:54,452] Trial 0 finished with value: 0.8749799518845229 and parameters: {'iterations': 427, 'depth': 10, 'learning_rate': 0.05020852418951797, 'l2_leaf_reg': 4.1401527535951255}. Best is trial 0 with value: 0.8749799518845229.
[I 2024-10-15 21:04:55,259] Trial 1 finished with value: 0.8819299652499332 and parameters: {'iterations': 162, 'depth': 7, 'learning_rate': 0.08717644919719023, 'l2_leaf_reg': 4.543388325565493}. Best is trial 1 with value: 0.8819299652499332.
[I 2024-10-15 21:04:58,421] Trial 2 finished with value: 0.8842288158246457 and parameters: {'iterations': 231, 'depth': 9, 'learning_rate': 0.1662686729955037, 'l2_leaf_reg': 4.930801138552911}. Best is trial 2 with value: 0.8842288158246457.
[I 2024-10-15 21:04:59,651] Trial 3 finished with value: 0.8842822774659181 and parameters: {'iterations': 248, 'depth': 5, 'learning_rate': 0.09099628029492468, 'l2_leaf_reg': 3.614269835610246}. Best is trial 3 with value: 0.8842822774659181.
[I 2024-10-15 21:05

Best CatBoost params: {'iterations': 225, 'depth': 8, 'learning_rate': 0.17368752408635546, 'l2_leaf_reg': 1.7765324023906608}


In [19]:
# Train and evaluate models with best parameters from Optuna

# Random Forest
rf_best = RandomForestClassifier(**best_rf_params, random_state=42)
rf_best.fit(X_train_scaled, y_train)
y_pred_rf = rf_best.predict(X_test_scaled)
rf_accuracy = accuracy_score(y_test, y_pred_rf)
rf_f1 = f1_score(y_test, y_pred_rf)
print(f"Random Forest - Accuracy: {rf_accuracy:.4f}, F1 Score: {rf_f1:.4f}")

# XGBoost
xgb_best = XGBClassifier(**best_xgb_params, use_label_encoder=False, eval_metric='logloss', random_state=42)
xgb_best.fit(X_train_scaled, y_train)
y_pred_xgb = xgb_best.predict(X_test_scaled)
xgb_accuracy = accuracy_score(y_test, y_pred_xgb)
xgb_f1 = f1_score(y_test, y_pred_xgb)
print(f"XGBoost - Accuracy: {xgb_accuracy:.4f}, F1 Score: {xgb_f1:.4f}")

# LightGBM
lgbm_best = LGBMClassifier(**best_lgbm_params, random_state=42)
lgbm_best.fit(X_train_scaled, y_train)
y_pred_lgbm = lgbm_best.predict(X_test_scaled)
lgbm_accuracy = accuracy_score(y_test, y_pred_lgbm)
lgbm_f1 = f1_score(y_test, y_pred_lgbm)
print(f"LightGBM - Accuracy: {lgbm_accuracy:.4f}, F1 Score: {lgbm_f1:.4f}")

# CatBoost
catboost_best = CatBoostClassifier(**best_catboost_params, verbose=0, random_state=42)
catboost_best.fit(X_train_scaled, y_train)
y_pred_catboost = catboost_best.predict(X_test_scaled)
catboost_accuracy = accuracy_score(y_test, y_pred_catboost)
catboost_f1 = f1_score(y_test, y_pred_catboost)
print(f"CatBoost - Accuracy: {catboost_accuracy:.4f}, F1 Score: {catboost_f1:.4f}")


Random Forest - Accuracy: 0.8624, F1 Score: 0.9254
XGBoost - Accuracy: 0.8440, F1 Score: 0.9146
[LightGBM] [Info] Number of positive: 378, number of negative: 54
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000040 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 246
[LightGBM] [Info] Number of data points in the train set: 432, number of used features: 5
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.875000 -> initscore=1.945910
[LightGBM] [Info] Start training from score 1.945910
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

In [21]:
print(f"Random Forest - Accuracy: {rf_accuracy:.4f}, F1 Score: {rf_f1:.4f}")
print(f"XGBoost - Accuracy: {xgb_accuracy:.4f}, F1 Score: {xgb_f1:.4f}")
print(f"LightGBM - Accuracy: {lgbm_accuracy:.4f}, F1 Score: {lgbm_f1:.4f}")
print(f"CatBoost - Accuracy: {catboost_accuracy:.4f}, F1 Score: {catboost_f1:.4f}")


Random Forest - Accuracy: 0.8624, F1 Score: 0.9254
XGBoost - Accuracy: 0.8440, F1 Score: 0.9146
LightGBM - Accuracy: 0.8807, F1 Score: 0.9353
CatBoost - Accuracy: 0.8440, F1 Score: 0.9146


                Classifier  Accuracy  Precision    Recall  F1 Score  \
2                 LightGBM  0.834862   0.881188  0.936842  0.908163   
0            Random Forest  0.834862   0.888889  0.926316  0.907216   
1                  XGBoost  0.816514   0.878788  0.915789  0.896907   
6     Decision Tree (gini)  0.779817   0.890110  0.852632  0.870968   
3                 CatBoost  0.770642   0.880435  0.852632  0.866310   
8              Naive Bayes  0.770642   0.937500  0.789474  0.857143   
7  Decision Tree (entropy)  0.743119   0.876404  0.821053  0.847826   
5                KNN (k=3)  0.733945   0.892857  0.789474  0.837989   
4                KNN (k=5)  0.660550   0.902778  0.684211  0.778443   
9         Dummy Classifier  0.128440   0.000000  0.000000  0.000000   

   Time Taken (seconds)  
2              0.058355  
0              0.178539  
1              0.100754  
6              0.001682  
3              1.409023  
8              0.000512  
7              0.001987  
5              0.002913  
4              0.003150  
9              0.000158 



Grid Search Results - Best Accuracies:
Random Forest - Best Accuracy: 0.8638
Decision Tree (entropy) - Best Accuracy: 0.8492
LightGBM - Best Accuracy: 0.8349
Decision Tree (gini) - Best Accuracy: 0.8241
XGBoost - Best Accuracy: 0.8165
KNN (k=5) - Best Accuracy: 0.8003
KNN (k=3) - Best Accuracy: 0.8003
CatBoost - Best Accuracy: 0.7706
Naive Bayes - Best Accuracy: 0.7706
Dummy Classifier - Best Accuracy: 0.1284

Randomized Search Results - Best Accuracies:
Random Forest - Best Accuracy: 0.8677
Decision Tree (gini) - Best Accuracy: 0.8492
Decision Tree (entropy) - Best Accuracy: 0.8466
LightGBM - Best Accuracy: 0.8349
KNN (k=5) - Best Accuracy: 0.8280
KNN (k=3) - Best Accuracy: 0.8280
XGBoost - Best Accuracy: 0.8165
CatBoost - Best Accuracy: 0.7706
Naive Bayes - Best Accuracy: 0.7706
Dummy Classifier - Best Accuracy: 0.1284